In [1]:
# import library
import tensorflow as tf
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import csv

import pythainlp
import pythaispell
from gingerit.gingerit import GingerIt
from langdetect import detect
import nltk
from keras import *
from keras.utils import to_categorical
from pythainlp import word_tokenize
from pythainlp.corpus import thai_stopwords
from pythainlp.corpus import wordnet
from nltk.stem.porter import PorterStemmer
from nltk.corpus import words
from stop_words import get_stop_words
from sklearn.feature_extraction.text import CountVectorizer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics import confusion_matrix, classification_report
from pythainlp.corpus.common import thai_words
from pythainlp.tokenize import dict_trie
from pythainlp.tag.named_entity import ThaiNameTagger
from pythainlp.word_vector import get_model
from sklearn.model_selection import train_test_split

from sklearn.model_selection import train_test_split

Using TensorFlow backend.


In [2]:
# import data from Excel
df = pd.read_excel('./Data/All_Perfect_Data.xlsx',sheet_name=None)

In [3]:
df

OrderedDict([('Sheet0',
                    a  Category                                        Description
              0     0         0  SmartphonesSAMSUNG Galaxy A20s *ประกันศูนย์ 1ป...
              1     1         0  SmartphonesSamsung A30 Ram4/64GB (เครื่องศูนย์...
              2     2         0  SmartphonesSamsung Galaxy A10 Ram2/32GB จอ 6.2...
              3     3         0  SmartphonesSamsung Galaxy M30s (4/64GB) ( โทรศ...
              4     4         0  SmartphonesSamsung Galaxy A10 Ram2/32GB จอ 6.2...
              ..   ..       ...                                                ...
              821  75         0  สมาร์ทดีไวซ์ Newแก็ดเจ็ตเครื่องเล่นเกมคอมโซล N...
              822  76         0  สมาร์ทดีไวซ์ Newแก็ดเจ็ตเครื่องเล่นเกมคอมโซล N...
              823  77         0  สมาร์ทดีไวซ์ Newแก็ดเจ็ตเครื่องเล่นเกมคอมโซล N...
              824  78         0  สมาร์ทดีไวซ์ Newแก็ดเจ็ตเครื่องเล่นเกมคอมโซล N...
              825  79         0  สมาร์ทดีไวซ์ Newแก็ดเจ็ตเครื่อ

In [4]:
df0 = df['Sheet0']
df0.head()

a  Category                                        Description
0  0         0  SmartphonesSAMSUNG Galaxy A20s *ประกันศูนย์ 1ป...
1  1         0  SmartphonesSamsung A30 Ram4/64GB (เครื่องศูนย์...
2  2         0  SmartphonesSamsung Galaxy A10 Ram2/32GB จอ 6.2...
3  3         0  SmartphonesSamsung Galaxy M30s (4/64GB) ( โทรศ...
4  4         0  SmartphonesSamsung Galaxy A10 Ram2/32GB จอ 6.2...

In [5]:
df0.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 826 entries, 0 to 825
Data columns (total 3 columns):
a              826 non-null int64
Category       826 non-null int64
Description    826 non-null object
dtypes: int64(2), object(1)
memory usage: 19.5+ KB


# Process text

In [14]:
import re
import string

# word correction for EN
#parser = GingerIt()

# download stopwords of TH and EN
nltk.download('words')
th_stop = tuple(thai_stopwords())
en_stop = tuple(get_stop_words('en'))
p_stemmer = PorterStemmer()

# clean the text
def clean_text(msg): 
    
    # ลบ text ที่อยู่ใน []
    #msg = re.sub(r'[<*●•►【】✨✈✅#?>]','', str(msg))
    #msg = re.sub(r'✅','',msg)
    # ลบ hashtag
    #msg = re.sub(r'#','',msg)
    msg = re.sub(r"[^A-Za-z0-9ก-๙.]","", str(msg))
    msg = re.sub(r"SKU\d+TH\d+","",str(msg))
    msg = re.sub(r"[A-Za-z]{30,}","",str(msg))
    # Delete punctuation
    str_punc = string.punctuation.replace(".","")
    for c in str_punc:
        msg = re.sub(r'\{}'.format(c),'',str(msg))
    
    # ลบ separator เช่น \n \t
    msg = ' '.join(msg.split())
    
    return msg

# split to words from text
def split_word(text):
    words = word_tokenize(text,engine='attacut',keep_whitespace=False)

    # Remove stop words TH and EN
    words = [i for i in words if not i in th_stop and not i in en_stop]
    
    # รากศัพท์
    # EN
    #words = [p_stemmer.stem(i) for i in words]
    
    # TH
    tokens_temp=[]
    for i in words:
        w_syn = wordnet.synsets(i)
        if (len(w_syn)>0) and (len(w_syn[0].lemma_names('tha'))>0) and not (w_syn[0].lemma_names('tha')[0].isdigit()):
            tokens_temp.append(w_syn[0].lemma_names('tha')[0])
        else:
            tokens_temp.append(i)
    
    words = tokens_temp
    
    # delete whitespace
    #words = [i for i in words if not ' ' in i]

    return words

[nltk_data] Downloading package words to
[nltk_data]     C:\Users\super\AppData\Roaming\nltk_data...
[nltk_data]   Package words is already up-to-date!


In [7]:
des = df0['Description'].values
des[0]

'SmartphonesSAMSUNG Galaxy A20s *ประกันศูนย์ 1ปี* อุปกรณ์ในกล่อง หัวชาร์จ / สาย USB Type-CA20s ไม่ได้แถม หูฟัง / ฟิล์ม / เคส มาจากทางSAMSUNGทางร้านต้องแกะกล่องสินค้าเพื่อนำใบประกันส่งบริษัทผู้ผลิต****************************************แบรนด์ ซัมซุงSKU 568380632_TH-1042940038ประเภทของการรับประกัน มีการรับประกันกล้องหน้า (เมกะพิกเซล) 7 MP ขึ้นไปModel samsung galaxy A20sกล้องด้านหลัง 11-15MPระยะเวลาการรับประกัน 1 ปีBattery Capacity 4000 - 4999 mAh'

In [8]:
des_clean = [clean_text(txt) for txt in des]
des_clean

['SmartphonesSAMSUNGGalaxyA20sประกันศูนย์1ปีอุปกรณ์ในกล่องหัวชาร์จสายUSBTypeCA20sไม่ได้แถมหูฟังฟิล์มเคสมาจากทางSAMSUNGทางร้านต้องแกะกล่องสินค้าเพื่อนำใบประกันส่งบริษัทผู้ผลิตแบรนด์ซัมซุงประเภทของการรับประกันมีการรับประกันกล้องหน้าเมกะพิกเซล7MPขึ้นไปModelsamsunggalaxyA20sกล้องด้านหลัง1115MPระยะเวลาการรับประกัน1ปีBatteryCapacity40004999mAh',
 'SmartphonesSamsungA30Ram464GBเครื่องศูนย์ไทยมีประกันศูนย์1ปีสมาร์ทโฟนโทรศัพท์มือถือพร้อมระบบปฏิบัติการจอแสดงผลSuperAMOLED24bit16ล้านสีหน้าจอทรงหยดน้ำรูปตัวUInfinityUระบบสัมผัสMultiTouchกว้าง6.4นิ้วแนวทะแยงความละเอียด1080x2340พิกเซลCapacitiveระบบเซ็นเซอร์Sensorระบบตรวจสอบลายนิ้วมือFingerprintระบบจดจำใบหน้าFaceDetectionระบบหมุนภาพอัตโนมัติAccelerometerระบบเปิดปิดหน้าจออัตโนมัติขณะสนทนาProximityระบบปฏิบัติการAndroid9.0Pieหน่วยประมวลผลExynos7904OctaCoreความเร็ว1.8GHzหน่วยความจำ3264GBตัวเครื่องRAM34GBการ์ดหน่วยความจำmicroSDสูงสุด512GBกล้องดิจิตอล165ล้านพิกเซลDualCameraรูรับแสงขนาด1.7ไฟแฟลชLEDโฟกัสอัตโนมัติAutoFocusแตะเลือกจุดโฟกัสTouchFocusค้นหาใบหน้าอั

In [46]:
with open(r"./Data/data0.csv", 'w', encoding="utf-8") as csv_file:
    for row in pd_list:
        writer = csv.writer(csv_file)
        writer.writerow(row)

In [56]:
import xlsxwriter
xbook = xlsxwriter.Workbook('./Data/Test.xlsx')
xsheet = xbook.add_worksheet('Test')
i=0
for row in des_clean:
    xsheet.write(i, 0, des_clean[i])
    i = i+1
xbook.close()

In [9]:
len(des_clean)

826

In [11]:
des_token = [split_word(txt) for txt in des_clean]
des_token

[['SmartphonesSAMSUNGGalaxyA20sประกัน',
  'ศูนย์1',
  'ปี',
  'อุปกรณ์',
  'กล่อง',
  'หัวชาร์จสาย',
  'USBTypeCA20sไม่',
  'แถม',
  'หู',
  'ฟัง',
  'ฟิล์มเคสมาจาก',
  'SAMSUNG',
  'ร้าน',
  'แกะ',
  'กล่อง',
  'สินค้า',
  'ใบ',
  'ประกัน',
  'บริษัท',
  'ทำ',
  'แบรนด์',
  'ซัมซุง',
  'ชนิด',
  'ประกัน',
  'ประกัน',
  'กล้อง',
  'หน้า',
  'เมกะพิกเซล',
  '7MP',
  'ModelsamsunggalaxyA20sกล้อง',
  '1115',
  'เอ็ม',
  'พี',
  'กาล',
  'ประกัน',
  '1',
  'ปีBatteryCapacity40004999mAh'],
 ['SmartphonesSamsungA30Ram464',
  'GB',
  'เครื่อง',
  'ศูนย์',
  'ไท',
  'ประกัน',
  'ศูนย์1ปีสมาร์ทโฟน',
  'โทร',
  'มือถือ',
  'ระบบ',
  'จอ',
  'ผลSuperAMOLED24bit16',
  'ล้าน',
  'สีหน้า',
  'จอ',
  'หยด',
  'น้ำ',
  'รูป',
  'ตัว',
  'UInfinityUระบบ',
  'จับ',
  'MultiTouchกว้าง',
  '6',
  '.',
  '4',
  'นิ้ว',
  'แนว',
  'ทะแยง',
  'ละเอียด',
  '1080',
  'x',
  '2340',
  'พิกเซลCapacitiveระบบ',
  'เซ็นเซอร์Sensorระบบ',
  'เช็ค',
  'ลาย',
  'นิ้ว',
  'มือFingerprintระบบ',
  'จำ',
  'ใบ',
  'หน้า',


In [13]:
des_token_newmm = [split_word(txt) for txt in des_clean]
des_token_newmm

[['SmartphonesSAMSUNGGalaxyA',
  '20',
  'เอส',
  'ประกัน',
  'ศูนย์',
  '1',
  'ปี',
  'อุปกรณ์',
  'กล่อง',
  'หัว',
  'ชาร์จ',
  'สาย',
  'USBTypeCA',
  '20',
  'เอส',
  'แถม',
  'หูฟัง',
  'ฟิล์ม',
  'เคส',
  'มาจาก',
  'SAMSUNG',
  'ร้าน',
  'แกะ',
  'กล่อง',
  'สินค้า',
  'ใบ',
  'ประกัน',
  'บริษัทผู้ผลิต',
  'แบรนด์',
  'ซัมซุง',
  'ชนิด',
  'การรับประกัน',
  'การรับประกัน',
  'กล้อง',
  'หน้า',
  'เมกะ',
  'พิกเซล',
  '7',
  'MP',
  'ขึ้นไป',
  'ModelsamsunggalaxyA',
  '20',
  'เอส',
  'กล้อง',
  'ด้านหลัง',
  '1115',
  'MP',
  'ระยะเวลา',
  'การรับประกัน',
  '1',
  'ปี',
  'BatteryCapacity',
  '40004999',
  'mAh'],
 ['SmartphonesSamsungA',
  '30',
  'Ram',
  '464',
  'GB',
  'เครื่อง',
  'ศูนย์',
  'ไท',
  'ประกัน',
  'ศูนย์',
  '1',
  'ปี',
  'สมาร์ท',
  'โฟน',
  'มือถือ',
  'ระบบปฏิบัติการ',
  'จอแสดงผล',
  'SuperAMOLED',
  '24',
  'bit',
  '16',
  'ล้าน',
  'สี',
  'หน้าจอ',
  'หยดน้ำ',
  'รูป',
  'ตัว',
  'UInfinityU',
  'ระบบ',
  'จับ',
  'MultiTouch',
  '6.4',
  'นิ้ว',

In [61]:
from pythainlp.ulmfit import (
    process_thai,
    lowercase_all,
    rm_brackets,
    remove_space)
text = des[0]
text_processed = process_thai(text)

In [70]:
from pythainlp.tag import pos_tag

pos_tag([txt for txt in text_processed], corpus='orchid')

[('smartphonessamsung', 'NCMN'),
 ('galaxy', 'NCMN'),
 ('a', 'NCMN'),
 ('20', 'NCNM'),
 ('s', 'NCMN'),
 ('*', 'PUNC'),
 ('ประกัน', 'NCNM'),
 ('ศูนย์', 'DCNM'),
 ('1', 'NCNM'),
 ('ปี', 'CMTR'),
 ('*', 'PUNC'),
 ('อุปกรณ์', 'NCMN'),
 ('ใน', 'RPRE'),
 ('กล่อง', 'NCMN'),
 ('หัว', 'NCMN'),
 ('ชาร์จ', 'NCMN'),
 ('/', 'PUNC'),
 ('สาย', 'NCMN'),
 ('usb', 'NCMN'),
 ('type-ca', 'NCMN'),
 ('20', 'DCNM'),
 ('s', 'NCMN'),
 ('ไม่ได้', 'NEG'),
 ('แถม', 'VACT'),
 ('หูฟัง', 'NCMN'),
 ('/', 'PUNC'),
 ('ฟิล์ม', 'NCMN'),
 ('/', 'PUNC'),
 ('เคส', 'VATT'),
 ('มาจาก', 'NEG'),
 ('ทาง', 'NCMN'),
 ('samsung', 'NCMN'),
 ('ทาง', 'NCMN'),
 ('ร้าน', 'NCMN'),
 ('ต้อง', 'XVMM'),
 ('แกะ', 'VACT'),
 ('กล่อง', 'NCMN'),
 ('สินค้า', 'NCMN'),
 ('เพื่อ', 'JSBR'),
 ('นำ', 'VACT'),
 ('ใบ', 'NCMN'),
 ('ประกัน', 'ADVN'),
 ('ส่ง', 'VACT'),
 ('บริษัทผู้ผลิต', 'NCMN'),
 ('*', 'PUNC'),
 ('xxrep', 'NCMN'),
 ('แบรนด์', 'NCMN'),
 ('ซัม', 'NCMN'),
 ('ซุง', 'NCMN'),
 ('sku', 'NCMN'),
 ('568380632', 'DCNM'),
 ('_', 'PUNC'),
 ('th-', 'CMT